<a href="https://colab.research.google.com/github/araga2004/Image_Caption_Gen/blob/main/Image_caption_generator.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
from collections import defaultdict
import string
def document_load(filename):
  file = open(filename, 'r')
  text = file.read()
  file.close()
  return text
def get_images_and_captions(filename):
  document = document_load(filename)
  descriptions = defaultdict(list)
  lines = document.split('\n')
  #all the images and captions are seperated by a newline char
  for line in lines[:-1]:
    img_id, caption = line.split('\t')
    img_id = img_id[:-2]
    descriptions[img_id].append(caption)
  return descriptions
def clean_text(captions):
  table = str.maketrans('', '', string.punctuation)
  for img_id in captions:
    caps = captions[img_id]
    table2 = str.maketrans("-", " ")
    for i, img_caption in enumerate(caps):
      img_caption.translate(table2)
      word_list = img_caption.split()
      #Removing short words and punctuation marks
      word_list = [word.translate(table).lower() for word in word_list]
      word_list = [word for word in word_list if len(word) > 1]
      word_list = [word for word in word_list if (word.isalpha())]
      clean_caption = ' '.join(word_list)
      captions[img_id][i] = clean_caption
  return captions

In [ ]:
#Testing the above code with a randomly generated dictionary
captions = {
  '123456789012345': [
    'a example random sentence with numbers and punctuation marks.',
    'with numbers and punctuation marks like digit nine 9.',
    'seven eight nine ten random example sentence with numbers.',
    'example random sentence with numbers and punctuation marks!',
    'comma period question mark digit ten random sentence with numbers.'
  ],
  '987654321098765': [
    'seven eight nine ten example random sentence with numbers.',
    'with numbers and punctuation marks like comma period?',
    'digit seven eight nine ten example random sentence with numbers.',
    'example random sentence with a numbers and punctuation marks!',
    'example random sentence with numbers and punctuation marks.'
  ],
  '123098765432109': [
    'example random sentence with numbers and punctuation marks.',
    'with numbers and punctuation marks like digit nine!',
    'seven eight nine ten random example sentence with numbers.',
    'example random sentence with numbers and punctuation marks explanation!',
    'comma period question mark digit ten random sentence with numbers.'
  ],
  '456123789012345': [
    'example random sentence with numbers and punctuation marks.',
    'with numbers and punctuation marks like digit nine!',
    'seven eight nine ten random example sentence with numbers.',
    'example random sentence with numbers and punctuation marks!',
    'comma period question mark digit ten random sentence with numbers.'
  ],
  '654321098765432': [
    'example random sentence with numbers and punctuation marks!',
    'with numbers and punctuation marks like digit nine.',
    'seven eight nine ten example random sentence with numbers!',
    'example random sentence with numbers and punctuation marks?',
    'comma period question mark digit ten random sentence with numbers!'
  ]
}
clean_captions = clean_text(captions)
print(clean_captions)

{'123456789012345': ['example random sentence with numbers and punctuation marks', 'with numbers and punctuation marks like digit nine', 'seven eight nine ten random example sentence with numbers', 'example random sentence with numbers and punctuation marks', 'comma period question mark digit ten random sentence with numbers'], '987654321098765': ['seven eight nine ten example random sentence with numbers', 'with numbers and punctuation marks like comma period', 'digit seven eight nine ten example random sentence with numbers', 'example random sentence with numbers and punctuation marks', 'example random sentence with numbers and punctuation marks'], '123098765432109': ['example random sentence with numbers and punctuation marks', 'with numbers and punctuation marks like digit nine', 'seven eight nine ten random example sentence with numbers', 'example random sentence with numbers and punctuation marks explanation', 'comma period question mark digit ten random sentence with numbers'], 

In [ ]:
def build_vocab(descriptions):
  vocabulary = set()
  for key in descriptions:
    for line in descriptions[key]:
      vocabulary.update(line.split())
  return vocabulary
vocab = build_vocab(clean_captions)
print(vocab)
def description_filesave(descriptions, filename):
  lines = list()
  for img_id, captions in descriptions.items():
    for caption in captions:
      lines.append(img_id + '\t' + caption)
  data = "\n".join(lines)
  file = open(filename,"w")
  file.write(data)
  file.close()

{'ten', 'and', 'comma', 'with', 'numbers', 'like', 'question', 'example', 'period', 'mark', 'marks', 'random', 'seven', 'eight', 'punctuation', 'nine', 'digit', 'explanation', 'sentence'}


In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [ ]:
filepath = '/content/drive/My Drive/Flickr8k.token.txt'

descriptions = get_images_and_captions(filepath)
#print(descriptions)
clean_descriptions = clean_text(descriptions)
print(clean_descriptions)
#final vocabulary
vocabulary = build_vocab(clean_descriptions)
print(len(vocabulary))
vocab_size = len(vocabulary)
description_filesave(clean_descriptions, "descriptions.txt")


defaultdict(<class 'list'>, {'1000268201_693b08cb0e.jpg': ['child in pink dress is climbing up set of stairs in an entry way', 'girl going into wooden building', 'little girl climbing into wooden playhouse', 'little girl climbing the stairs to her playhouse', 'little girl in pink dress going into wooden cabin'], '1001773457_577c3a7d70.jpg': ['black dog and spotted dog are fighting', 'black dog and tricolored dog playing with each other on the road', 'black dog and white dog with brown spots are staring at each other in the street', 'two dogs of different breeds looking at each other on the road', 'two dogs on pavement moving toward each other'], '1002674143_1b742ab4b8.jpg': ['little girl covered in paint sits in front of painted rainbow with her hands in bowl', 'little girl is sitting in front of large painted rainbow', 'small girl in the grass plays with fingerpaints in front of white canvas with rainbow on it', 'there is girl with pigtails sitting in front of rainbow painting', 'youn

In [ ]:
from keras.applications.xception import Xception, preprocess_input
from pickle import dump, load
from tqdm import tqdm_notebook as tqdm
from PIL import Image
import os
import numpy as np
tqdm().pandas()
dataset_images = "/content/drive/My Drive/Flicker8k_Dataset"
def extract_features(directory):
        model = Xception( include_top=False, pooling='avg' )
        features = {}
        for img in tqdm(os.listdir(directory)):
            filename = directory + "/" + img
            image = Image.open(filename)
            image = image.resize((299,299))
            image = np.expand_dims(image, axis=0)
            #image = preprocess_input(image)
            image = image/127.5
            image = image - 1.0

            feature = model.predict(image)
            features[img] = feature
        return features

#2048 feature vector
features = extract_features(dataset_images)
dump(features, open("features.p","wb"))

In [ ]:
from pickle import dump, load
features = load(open("/content/drive/My Drive/features.p","rb"))
print(features["2258277193_586949ec62.jpg"])

KeyError: '2258277193_586949ec62.jpg'

In [65]:
train_photo_names = '/content/drive/My Drive/Flickr_8k.trainImages.txt'
def photo_names(train_photos_names):
  file = document_load(train_photos_names)
  photos = file.splitlines()
  return photos
photos = photo_names(train_photo_names)
#print(photos[-1])
def load_clean_descriptions(filename, photos):
    file = document_load(filename)
    descriptions = defaultdict(list)
    all_captions = file.split("\n")
    for caption in all_captions:
        words = caption.split()
        image, image_caption = words[0], words[1:]
        #adding "<start> and <end> keywords to our captions"
        if image in photos:
          desc = '<start> ' + " ".join(image_caption) + ' <end>'
          descriptions[image].append(desc)
    return descriptions
train_imgs = photo_names(train_photo_names)
train_descriptions = load_clean_descriptions("descriptions.txt", train_imgs)
#print(train_imgs)
print(train_descriptions)
print(len(train_descriptions))



defaultdict(<class 'list'>, {'1000268201_693b08cb0e.jpg': ['<start> child in pink dress is climbing up set of stairs in an entry way <end>', '<start> girl going into wooden building <end>', '<start> little girl climbing into wooden playhouse <end>', '<start> little girl climbing the stairs to her playhouse <end>', '<start> little girl in pink dress going into wooden cabin <end>'], '1001773457_577c3a7d70.jpg': ['<start> black dog and spotted dog are fighting <end>', '<start> black dog and tricolored dog playing with each other on the road <end>', '<start> black dog and white dog with brown spots are staring at each other in the street <end>', '<start> two dogs of different breeds looking at each other on the road <end>', '<start> two dogs on pavement moving toward each other <end>'], '1002674143_1b742ab4b8.jpg': ['<start> little girl covered in paint sits in front of painted rainbow with her hands in bowl <end>', '<start> little girl is sitting in front of large painted rainbow <end>', 

In [66]:
def dict_to_list(descriptions):
    all_desc = []
    for key in descriptions.keys():
        [all_desc.append(d) for d in descriptions[key]]
    return all_desc
def max_length(descriptions):
    desc_list = dict_to_list(descriptions)
    return max(len(d.split()) for d in desc_list)

max_length = max_length(descriptions)
max_length

32

**Tokenization**

In [67]:
#converting dictionary to clean list of descriptions
def dict_to_list(descriptions):
    all_desc = []
    for key in descriptions.keys():
        [all_desc.append(d) for d in descriptions[key]]
    return all_desc

#creating tokenizer class
#this will vectorise text corpus
#each integer will represent token in dictionary

from keras.preprocessing.text import Tokenizer

def create_tokenizer(descriptions):
    desc_list = dict_to_list(descriptions)
    tokenizer = Tokenizer()
    tokenizer.fit_on_texts(desc_list)
    return tokenizer

# give each word an index, and store that into tokenizer.p pickle file
tokenizer = create_tokenizer(train_descriptions)
dump(tokenizer, open('tokenizer.p', 'wb'))
vocab_size = len(tokenizer.word_index) + 1
vocab_size

7577

In [ ]:
def load_features(photos):
    #loading all features
    all_features = load(open("/content/drive/My Drive/features.p","rb"))
    #selecting only needed features
    features = {k:all_features[k] for k in photos}
    return features
if "1022454332_6af2c1449a.jpg" in train_imgs:
  print("ya")
train_features = load_features(train_imgs)
#print((train_features["1022454332_6af2c1449a.jpg"]).shape)


In [68]:
from keras.preprocessing.sequence import pad_sequences
from keras.utils import to_categorical
import numpy as np
def data_generator(descriptions, features, tokenizer, max_length):
    while True:
        for key, description_list in descriptions.items():
            feature = features[key][0]
            input_image, input_sequence, output_word = create_sequences(tokenizer, max_length, description_list, feature)
            yield [[input_image, input_sequence], output_word]
def create_sequences(tokenzier, max_length, descriptions, feature):
  X1, X2, y = list(), list(), list()
  for desc in descriptions:
    sequence_list = tokenizer.texts_to_sequences([desc])
    seq = sequence_list[0]
    for i in range(1, len(seq)):
      feed = seq[:i]
      word_predict = seq[i]
      feed = pad_sequences([feed], maxlen = max_length)[0]
      word_predict = to_categorical([word_predict], num_classes = vocab_size)[0]
      X1.append(feature)
      X2.append(feed)
      y.append(word_predict)
  return np.array(X1), np.array(X2), np.array(y)
[a, b], c = next(data_generator(train_descriptions, train_features, tokenizer, max_length))
a.shape, b.shape, c.shape


((47, 2048), (47, 32), (47, 7577))

In [63]:
print(train_descriptions["1022454332_6af2c1449a.jpg"])

['<start> child and woman are at waters edge in big city <end>', '<start> large lake with lone duck swimming in it with several people around the edge of it <end>', '<start> little boy at lake watching duck <end>', '<start> young boy waves his hand at the duck in the water surrounded by green park <end>', '<start> two people are at the edge of lake facing the water and the city skyline <end>']


In [60]:
from keras.layers import add
from keras.models import Model, load_model
from keras.layers import Input, Dense, LSTM, Embedding, Dropout
from keras.utils import plot_model
max_length = 32
def define_model(vocab_size, max_length):
  input_feature = Input(shape=(2048,))
  in1 = Dropout(0.5)(input_feature)
  in2 = Dense(256, activation='relu')(in1)

  input_sequence = Input(shape=(max_length,))
  se1 = Embedding(vocab_size, 256, mask_zero=True)(input_sequence)
  se2 = Dropout(0.5)(se1)
  se3 = LSTM(256)(se2)

  decoder1 = add([in2, se3])
  decoder2 = Dense(256, activation='relu')(decoder1)
  outputs = Dense(vocab_size, activation='softmax')(decoder2)

  model = Model(inputs=[input_feature, input_sequence], outputs=outputs)
  model.compile(loss='categorical_crossentropy', optimizer='adam')
  print(model.summary())
  plot_model(model, to_file='model.png', show_shapes=True)
  return model

In [69]:
import os
max_length = 32
model = define_model(vocab_size, max_length)
epochs = 10
steps = len(train_descriptions)
for i in range(1, epochs):
    generator = data_generator(train_descriptions, train_features, tokenizer, max_length)
    model.fit(data_generator(train_descriptions, train_features, tokenizer, max_length), epochs=1, steps_per_epoch= steps, verbose=1)
    model.save("models/model_" + str(i) + ".h5")
    print(i)

Model: "model_2"
__________________________________________________________________________________________________
 Layer (type)                Output Shape                 Param #   Connected to                  
 input_6 (InputLayer)        [(None, 32)]                 0         []                            
                                                                                                  
 input_5 (InputLayer)        [(None, 2048)]               0         []                            
                                                                                                  
 embedding_2 (Embedding)     (None, 32, 256)              1939712   ['input_6[0][0]']             
                                                                                                  
 dropout_4 (Dropout)         (None, 2048)                 0         ['input_5[0][0]']             
                                                                                            

KeyboardInterrupt: 